# CC+SN jointfit - AvERA

#### Import libraries

In [ ]:
import os
import numpy as np
import matplotlib.pyplot as plt
from scipy.interpolate import interp1d
import numba
from numba import njit, float64, int32
import dynesty
from dynesty.utils import quantile
from dynesty import plotting as dyplot
import time

#### Parameters

In [ ]:
prefix    = 'CC_SN_joint_AvERA'                 # String that is appended to the generated filenames.
params    = [r'$H_0$', r'gran.']                # Formatted names of the free parameters as they will appear in the corner plot.
prior     = np.array([[50.,80.], [135.,1080.]]) # Prior intervals for the parameters listed in 'params'.
ndim      = len(params)                         # Dimension of the parameter space.
quantiles = [0.16,  0.50, 0.84 ]                # Quantiles used for best-fit parameter values and uncertainties.
os.makedirs('results', exist_ok=True)           # Initialize directories for result files and corner plots.
os.makedirs('graphs',  exist_ok=True)

#### Load input data
The CC dataset, covariance matrix, and the AvERA simulation output Logfiles are available in the accompanying Zenodo repository. <br>
The Pantheon+ SN dataset and covariance matrix can be downloaded from: <br>
https://github.com/PantheonPlusSH0ES/DataRelease/blob/main/Pantheon%2B_Data/4_DISTANCES_AND_COVAR/Pantheon%2BSH0ES.dat. <br>
https://github.com/PantheonPlusSH0ES/DataRelease/blob/main/Pantheon%2B_Data/4_DISTANCES_AND_COVAR/Pantheon%2BSH0ES_STAT%2BSYS.cov <br>
<br>
From he Pantheon+ SNIa database the following columns are used in the analysis: <br>
$\quad$ $\quad$ #3 : zHD - Hubble Diagram Redshift (with CMB and VPEC corrections), <br>
$\quad$ $\quad$ #13: CEPH_DIST - cepheid calculated absolute distance to host (uncertainty is incorporated in covariance matrix .cov), <br>
$\quad$ $\quad$ #14: IS_CALIBRATOR - binary to designate if this SN is in a host that has an associated cepheid distance, <br>
$\quad$ $\quad$ #20: mB - SALT2 uncorrected brightness, <br>
$\quad$ $\quad$ #18: x1 - SALT2 stretch, <br>
$\quad$ $\quad$ #16: c - SALT2 color, <br>
$\quad$ $\quad$ #35: HOST_LOGMASS - Host Galaxy Log Stellar Mass, <br>
$\quad$ $\quad$ #44: biasCor_m_b - Bias correction applied to brightness m_b. <br>
<br>
Source for $\tau$ (the step width used when determining $\delta_{\textrm{host}}$): <br>
https://github.com/PantheonPlusSH0ES/DataRelease/tree/main/Pantheon%2B_Data/5_COSMOLOGY/chains

In [ ]:
# Directory of the input files used, including the CC dataset, covariance matrix, and AvERA simulation Logfiles
dir_home = os.getcwd()
dir_data = dir_home + '/../data_files/'

In [ ]:
########## CC ##########

CC_Hz_data_file  = dir_data + 'Hz_data_MM22_kieg.dat'
CC_cov_data_file = dir_data + 'data_MM20.dat'
z_CC, Hz_CC, errHz  = np.genfromtxt(CC_Hz_data_file, comments='#', usecols=(0,1,2), unpack=True, delimiter=',')
zmod, imf, slib, sps, spsooo = np.genfromtxt(CC_cov_data_file, comments='#', usecols=(0,1,2,3,4), unpack=True)

# Estimate CC covariance matrix:
Cov_CC_diag = np.zeros((len(z_CC), len(z_CC)), dtype='float64') 
for i in range(len(z_CC)):
    Cov_CC_diag[i,i] = errHz[i]**2

imf_intp      = np.interp(z_CC, zmod, imf   )/100
slib_intp     = np.interp(z_CC, zmod, slib  )/100
sps_intp      = np.interp(z_CC, zmod, sps   )/100
spsooo_intp   = np.interp(z_CC, zmod, spsooo)/100
Cov_CC_imf    = np.zeros((len(z_CC), len(z_CC)), dtype='float64')
Cov_CC_slib   = np.zeros((len(z_CC), len(z_CC)), dtype='float64')
Cov_CC_sps    = np.zeros((len(z_CC), len(z_CC)), dtype='float64')
Cov_CC_spsooo = np.zeros((len(z_CC), len(z_CC)), dtype='float64')

for i in range(len(z_CC)):
    for j in range(len(z_CC)):
        Cov_CC_imf[i,j]    = Hz_CC[i] * imf_intp[i]    * Hz_CC[j] * imf_intp[j]
        Cov_CC_slib[i,j]   = Hz_CC[i] * slib_intp[i]   * Hz_CC[j] * slib_intp[j]
        Cov_CC_sps[i,j]    = Hz_CC[i] * sps_intp[i]    * Hz_CC[j] * sps_intp[j]
        Cov_CC_spsooo[i,j] = Hz_CC[i] * spsooo_intp[i] * Hz_CC[j] * spsooo_intp[j]
Cov_CC        = Cov_CC_spsooo + Cov_CC_imf + Cov_CC_diag
Cov_CC_inv    = np.linalg.inv(Cov_CC)


########## SN ##########

SN_data_file     = dir_data + 'Pantheon+SH0ES.dat'
SN_cov_data_file = dir_data + 'Pantheon+SH0ES_STAT+SYS.cov'
z_SN, mu_calib, calib, mB, x1, co, m_host, d_bias = np.genfromtxt(SN_data_file, comments='#', skip_header = True, usecols=(2,12,13,19,17,15,34,43), unpack=True, delimiter=' ')

# SN nuisance parameters are fixed -> the measurement distance moduli (Mu_SN) can be pre-calculated
tau    = 0.0697186
MB     = -19.199663
alpha  = 0.146365
beta   = 2.942802
gamma  = 0.009890

d_host = gamma * 1/(1 + np.exp((m_host-10)/tau)) - gamma/2
mu_SN  = mB + alpha * x1 - beta * co - MB - d_bias + d_host

# SN covariance matrix
Cov_SN_raw    = np.genfromtxt(SN_cov_data_file)
Cov_SN        = Cov_SN_raw[1:].reshape(int(Cov_SN_raw[0]),int(Cov_SN_raw[0]))
Cov_SN_inv    = np.linalg.inv(Cov_SN)
del Cov_SN_raw

In [ ]:
########## AvERA + interpolations ##########

granuls = [135, 320, 625, 1080]
grans   = np.arange(granuls[0], granuls[-1] + 1)  # 135 to 1080 inclusive

# Read original AvERA data
# Columns of the Logfile: t[Gy], error, h[Gy], a, z, H[km/s/Mpc], q, Omega_m_eff
z_Av_orig_list = []
Hz_Av_orig_list = []
z_Av_all = []

for g in granuls:
    filename = dir_data + f'HSTART1191_100Mpc_{g}k_s08159_IC_LCDM_Logfile.dat'
    z_vals, Hz_vals = np.genfromtxt(filename, comments='#', usecols=(4, 5), unpack=True)
    z_Av_orig_list.append(z_vals)
    Hz_Av_orig_list.append(Hz_vals)
    z_Av_all.extend(z_vals[:-1])  # drop last z < 0 value

# Create common redshift grid (z_Av), add z=0, and restrict to shared z-range
z_Av_all = sorted(set(z_Av_all))
z_Av = np.array([0.0] + z_Av_all)
zmax_common = min([max(z) for z in z_Av_orig_list])
z_Av = z_Av[z_Av <= zmax_common]

# Interpolate H(z) on z_Av for each granulation
Hz_Av_interp = []

for z_vals, Hz_vals in zip(z_Av_orig_list, Hz_Av_orig_list):
    Hz_func = interp1d(z_vals, Hz_vals, kind='linear', fill_value="extrapolate")
    Hz_interp_vals = Hz_func(z_Av)
    Hz_Av_interp.append(Hz_interp_vals)

Hz_Av_interp = np.array(Hz_Av_interp)  # shape: (4, len(z_Av))

# Build full Hz(z, granulation) matrix by interpolating along granulation axis
Hz_Av_matrix = np.array([
    interp1d(granuls, Hz_Av_interp[:, i], kind='linear', fill_value="extrapolate")(grans)
    for i in range(len(z_Av))
])  # shape: (len(z_Av), len(grans))

# Get H0 from z=0 row (first row of Hz_Av_matrix)
H0_all_grans = Hz_Av_matrix[0, :]  # shape: (len(grans),)



####### CC E(z):
# Step 1: Interpolate H(z) at z_CC for each granulation
CC_Hz_matrix = np.array([
    interp1d(z_Av, Hz_Av_matrix[:, j], kind='linear', fill_value="extrapolate")(z_CC)
    for j in range(len(grans))
]).T  # shape: (len(z_CC), len(grans))

# Step 2: Normalize to get E(z)
CC_Ez_matrix = CC_Hz_matrix / H0_all_grans  # broadcasting across columns



####### SN integral(1/E(z)):
SN_integral_matrix = []

Hz_interp_funcs = [
    interp1d(z_Av, Hz_Av_matrix[:, j], kind='linear', fill_value="extrapolate")
    for j in range(len(grans))
]

for z in z_SN:
    # Select z_Av points up to z_SN
    mask = z_Av <= z
    z_sub = z_Av[mask]                      # (n,)
    Hz_sub = Hz_Av_matrix[mask, :]          # (n, len(grans))

    # Interpolate H(z_SN) from z_Av
    Hz_SN = np.array([Hz_interp_funcs[j](z) for j in range(len(grans))])  # shape: (len(grans),)

    # Extend z and Hz arrays
    z_ext = np.append(z_sub, z)
    Hz_ext = np.vstack((Hz_sub, Hz_SN))     # shape: (n+1, len(grans))

    Ez_ext = Hz_ext / H0_all_grans          # shape: (n+1, len(grans))
    integral = np.trapz(1.0 / Ez_ext, x=z_ext, axis=0)
    SN_integral_matrix.append(integral)

SN_integral_matrix = np.array(SN_integral_matrix)  # shape: (len(z_SN), len(grans))

#### Define functions for likelihood analysis

In [ ]:
@njit("float64[::1](float64[::1], float64[:, ::1])", fastmath=True)
def Hz_model_CC_numba(p, Ez_CC):
    H0, gran = p
    gran_index = int(round(gran)) - 135
    Ez = Ez_CC[:, gran_index]
    Hz_model_CC = H0 * Ez
    return Hz_model_CC

def Hz_model_CC(p, Ez_CC):
    p     = np.ascontiguousarray(p, dtype=np.float64)
    Ez_CC = np.ascontiguousarray(Ez_CC, dtype=np.float64)
    return Hz_model_CC_numba(p, Ez_CC)


@njit("Tuple((float64[::1], float64[::1]))(float64[::1], float64[::1], float64[::1], float64[::1], float64[:, ::1])", fastmath=True)
def Mu_model_SN_numba(p, z_SN, mu_calib, calib, integr): 
    H0, gran = p
    c = 299792458.0
    gran_index = int(round(gran)) - 135
    integ = integr[:, gran_index]
    dL = (1.0 + z_SN) * (c / H0) * integ
    mu_model_calc_SN = 5.0 * np.log10(dL * 100.0)
    mu_model_SN = mu_calib * calib + mu_model_calc_SN * (1.0 - calib)
    return mu_model_SN, mu_model_calc_SN

def Mu_model_SN(p, z_SN, mu_calib, calib, integr):
    p         = np.ascontiguousarray(p, dtype=np.float64)
    z_SN      = np.ascontiguousarray(z_SN, dtype=np.float64)
    mu_calib  = np.ascontiguousarray(mu_calib, dtype=np.float64)
    calib     = np.ascontiguousarray(calib, dtype=np.float64)
    integr    = np.ascontiguousarray(integr, dtype=np.float64)
    return Mu_model_SN_numba(p, z_SN, mu_calib, calib, integr)


@njit("float64(float64[::1], float64[::1], float64[::1], float64[::1], float64[:, ::1], float64[::1], float64[:, ::1], float64[:, ::1], float64[::1], float64[:, ::1])", fastmath=True)
def loglike_numba(p, z_SN, mu_calib, calib, integr, mu_SN, Cov_SN_inv, Ez_CC, Hz_CC, Cov_CC_inv):
    mu_model_SN = Mu_model_SN_numba(p, z_SN, mu_calib, calib, integr)[0]
    residual_SN = mu_SN - mu_model_SN
    chi2_SN     = np.dot(residual_SN, np.dot(Cov_SN_inv, residual_SN))
    Hz_model_CC = Hz_model_CC_numba(p, Ez_CC)
    residual_CC = Hz_CC - Hz_model_CC
    chi2_CC     = np.dot(residual_CC, np.dot(Cov_CC_inv, residual_CC))
    return -0.5 * (chi2_SN/(1701-2) + chi2_CC/(33-2))
    
def loglike(p, z_SN, mu_calib, calib, integr, mu_SN, Cov_SN_inv, Ez_CC, Hz_CC, Cov_CC_inv):
    p          = np.ascontiguousarray(p, dtype=np.float64)
    z_SN       = np.ascontiguousarray(z_SN, dtype=np.float64)
    mu_calib   = np.ascontiguousarray(mu_calib, dtype=np.float64)
    calib      = np.ascontiguousarray(calib, dtype=np.float64)
    integr     = np.ascontiguousarray(integr, dtype=np.float64)
    mu_SN      = np.ascontiguousarray(mu_SN, dtype=np.float64)
    Cov_SN_inv = np.ascontiguousarray(Cov_SN_inv, dtype=np.float64)
    Ez_CC      = np.ascontiguousarray(Ez_CC, dtype=np.float64)
    Hz_CC      = np.ascontiguousarray(Hz_CC, dtype=np.float64)
    Cov_CC_inv = np.ascontiguousarray(Cov_CC_inv, dtype=np.float64)
    return loglike_numba(p, z_SN, mu_calib, calib, integr, mu_SN, Cov_SN_inv, Ez_CC, Hz_CC, Cov_CC_inv)

def ptform(u):
    H0_min, H0_max = prior[0]
    gran_min, gran_max = int(prior[1, 0]), int(prior[1, 1])
    H0 = H0_min + u[0] * (H0_max - H0_min)
    gran = gran_min + int(np.floor(u[1] * (gran_max - gran_min + 1)))
    return np.array([H0, gran], dtype=np.float64)

#### Results

In [ ]:
# Determining best-fit parameter values with uncertainties,
# using percentiles of the parameter posteriors defined in the 'quantiles' list.
def optparams(samples, weights):
    lo, me, hi = [], [], []
    for i in range(ndim):
        q_lo, q_me, q_hi = quantile(samples[:, i], quantiles, weights=weights)
        lo.append(q_lo)
        me.append(q_me)
        hi.append(q_hi)
    lo = np.array(lo)
    me = np.array(me)
    hi = np.array(hi)
    return np.stack([me, me - lo, hi - me], axis=1)

# Corner plot of the posterior parameter distributions.
def plot_corner(results, filename):
    fig, axes = dyplot.cornerplot(
        results,
        show_titles=True,
        labels=params,
        quantiles=quantiles,
        title_quantiles=quantiles,
        title_fmt='.3f'
    )
    fig.savefig(filename)


# Displaying a summary of the results and the corner plot, and saving the result files.
def Results(results):
    
    results.summary()
    print("=======")
    
    samples       = results.samples
    weights       = np.exp(results.logwt - results.logz[-1])
    OptParams     = optparams(samples, weights) 

    np.savetxt('results/Samples_'  +prefix+'.txt',      samples,      delimiter='\t')
    np.savetxt('results/Weights_'  +prefix+'.txt',      weights,      delimiter='\t')
    plot_corner(results, 'graphs/Posteriors_'+prefix+'.pdf')

#### RunThis

In [ ]:
def RunThis():
    sampler = dynesty.DynamicNestedSampler(lambda p: loglike(p, z_SN, mu_calib, calib, SN_integral_matrix, mu_SN, Cov_SN_inv, CC_Ez_matrix, Hz_CC, Cov_CC_inv), ptform, ndim)
    sampler.run_nested()
    Results(results=sampler.results)

In [ ]:
RunThis()